In [52]:
# Import required modules
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import yfinance as yf
import plotly.express as px

# Ticker list to download
tickers = 'SPY QQQ TLT AAPL MSFT GOOG AMZN NFLX NVDA TSLA'


# Have some fun here and explore what stocks this strategy works for and why...
ticker = 'SPY'
# ticker = 'TLT'
# ticker = 'NVDA'
# ticker = 'AAPL'
# ticker = 'INTC'
# Download data from Yahoo-Finance

data = yf.download(
    tickers = ticker,
    start="2020-01-01", # From what point do we want to start getting stock data
    end="2024-04-30", # From what point do we want to stop getting stock data
    interval = "1d", # The sample rate of the data one stock data every day
    ignore_tz=True,
    auto_adjust=True, # Adjust all fields by splits and dividends
)


[*********************100%***********************]  1 of 1 completed


In [53]:
close_stock = data['Close'].copy()
close_stock = pd.DataFrame(close_stock)
close_stock.columns = ['close']
df = data['Close'].copy()
print(df)

Ticker                            SPY
Date                                 
2020-01-02 00:00:00+00:00  302.208679
2020-01-03 00:00:00+00:00  299.920258
2020-01-06 00:00:00+00:00  301.064423
2020-01-07 00:00:00+00:00  300.217957
2020-01-08 00:00:00+00:00  301.817993
...                               ...
2024-04-23 00:00:00+00:00  502.482697
2024-04-24 00:00:00+00:00  502.244202
2024-04-25 00:00:00+00:00  500.336243
2024-04-26 00:00:00+00:00  505.076385
2024-04-29 00:00:00+00:00  506.865082

[1088 rows x 1 columns]


In [54]:
df.describe()

Ticker          SPY
count   1088.000000
mean     389.204945
std       60.724802
min      208.617615
25%      356.089409
50%      397.610367
75%      429.497032
max      519.892944

In [59]:
# You can either do a expanding mean, which caluclates the mean from the beginning or a rolling mean giving the mean for the past ten days.
#Expanding mean
#close_stock["Mean Price"] =  close_stock["close"].expanding().mean()
#close_stock["Standard Deviation"] = close_stock["close"].expanding().std()
#Rolling mean
close_stock["Mean Price"] = close_stock.close.rolling(window = 10).mean()
close_stock["Standard Deviation"] = close_stock["close"].rolling(window=10).std()

close_stock['daily_change'] = close_stock.close.pct_change().fillna(0)

close_stock = close_stock.fillna(302)
close_stock['Z-Score'] = (close_stock["close"] - close_stock["Mean Price"])/(close_stock["Standard Deviation"])
print(close_stock)

close_stock = close_stock.assign(
    
                signal =  np.where(close_stock["Z-Score"] > 2, -1,(np.where(close_stock["Z-Score"] < -2,1,0)))
            )
close_stock['signal'] = close_stock['signal'].shift(1,fill_value = 0)
close_stock['Mean Reversion'] = close_stock['daily_change'] * close_stock['signal']

                                close  Mean Price  Standard Deviation  \
Date                                                                    
2020-01-02 00:00:00+00:00  302.208679  302.000000          302.000000   
2020-01-03 00:00:00+00:00  299.920258  302.000000          302.000000   
2020-01-06 00:00:00+00:00  301.064423  302.000000          302.000000   
2020-01-07 00:00:00+00:00  300.217957  302.000000          302.000000   
2020-01-08 00:00:00+00:00  301.817993  302.000000          302.000000   
...                               ...         ...                 ...   
2024-04-23 00:00:00+00:00  502.482697  501.990811            7.132012   
2024-04-24 00:00:00+00:00  502.244202  501.125269            6.420418   
2024-04-25 00:00:00+00:00  500.336243  499.683356            4.282363   
2024-04-26 00:00:00+00:00  505.076385  499.425980            3.800588   
2024-04-29 00:00:00+00:00  506.865082  499.983463            4.456669   

                           daily_change   Z-Score 

In [56]:
# Get the cumulative product over the 4 years for both our strategy and when we just buy and hold
cumprod_strategy = (1 + close_stock['Mean Reversion']).cumprod()
cumprod_buy_and_hold = (1 + close_stock['daily_change']).cumprod()
cumprod_signals = pd.DataFrame(dict(
    strategy = cumprod_strategy,
    buy_hold = cumprod_buy_and_hold
))

# Scale our money by the cumulative products
px.line(100 * cumprod_signals)

In [128]:
#Backtesting for differnt values.
data = yf.download(
    tickers = ticker,
    start="2020-01-01", # From what point do we want to start getting stock data
    end="2024-04-30", # From what point do we want to stop getting stock data
    interval = "1d", # The sample rate of the data one stock data every day
    ignore_tz=True,
    auto_adjust=True, # Adjust all fields by splits and dividends
)
close_stock = data['Close'].copy()
close_stock = pd.DataFrame(close_stock)
close_stock.columns = ['close']
results = []
for j  in range(1,39):
    ZScore = 1 + j/30
    for Days in range(10,60):
    
        close_stock["Mean Price"] = close_stock["close"].rolling(window=Days).mean().fillna(330)
        
        #close_stock["Mean Price"] = close_stock["close"].rolling(window = Days).mean()
        
        
        close_stock["Standard Deviation"] = close_stock["close"].rolling(window=Days).std()
        close_stock['daily_change'] = close_stock.close.pct_change().fillna(0.01)
        
        
        close_stock['Z-Score'] = (close_stock["close"] - close_stock["Mean Price"])/(close_stock["Standard Deviation"])
        
        close_stock = close_stock.assign(
    
                    signal =  np.where(close_stock["Z-Score"] > ZScore, -1,(np.where(close_stock["Z-Score"] < -(ZScore),1,0)))
                )
        close_stock['signal'] = close_stock['signal'].shift(1,fill_value = 0)
        close_stock['Mean Reversion'] = close_stock['daily_change'] * close_stock['signal']
    
    
        cumprod_buy_and_hold = (1 + close_stock['daily_change']).cumprod()
        cumprod_strategy = (1 + close_stock['Mean Reversion']).cumprod()
        max_peaks = cumprod_strategy.cummax()
        drawdown = (cumprod_strategy - max_peaks) / max_peaks
        

        annualized_returns = (1 + (close_stock[['daily_change', 'Mean Reversion']]).mean())**252 - 1
        annualized_std_deviation = close_stock[['daily_change', 'Mean Reversion']].std() * np.sqrt(252)
        max_drawdown = (drawdown.min() - 1) * -1

        perf = dict(
                ZScore = ZScore,
                Days = Days,
                annualized_returns = annualized_returns['Mean Reversion'],
                annualized_std_deviation = annualized_std_deviation['Mean Reversion'],
                annualized_returns_buy_and_hold = annualized_returns['daily_change'],
                max_drawdown = max_drawdown,
                cumprod_buy_and_hold = cumprod_buy_and_hold.iloc[-1],
                cumprod_strategy = cumprod_strategy.iloc[-1],
                strategy_sharpe_ratio = (annualized_returns['Mean Reversion'] - 0.05) / annualized_std_deviation['Mean Reversion'],
               
                buy_hold_sharpe_ratio = (annualized_returns['daily_change'] - 0.05) / annualized_std_deviation['daily_change']
            
                )

        results.append(perf)
    

results = pd.DataFrame(results)
print(results)
results.sort_values('annualized_returns', ascending=False).head()
eval_metric = 'strategy_sharpe_ratio'

df_mat = results.pivot(index = 'Days', columns = 'ZScore', values=eval_metric)

fig = px.imshow(df_mat,
                color_continuous_scale = 'RdYlGn',
                aspect = 'auto')

fig.update_layout(
    title=eval_metric,
    xaxis_title='ZScore',
    yaxis_title='Days',
)

fig
risk = monthly_ret.std()



[*********************100%***********************]  1 of 1 completed


                                close  Mean Price
Date                                             
2020-01-02 00:00:00+00:00  302.208679  330.000000
2020-01-03 00:00:00+00:00  299.920258  330.000000
2020-01-06 00:00:00+00:00  301.064423  330.000000
2020-01-07 00:00:00+00:00  300.217957  330.000000
2020-01-08 00:00:00+00:00  301.817993  330.000000
...                               ...         ...
2024-04-23 00:00:00+00:00  502.482697  501.990811
2024-04-24 00:00:00+00:00  502.244202  501.125269
2024-04-25 00:00:00+00:00  500.336243  499.683356
2024-04-26 00:00:00+00:00  505.076385  499.425980
2024-04-29 00:00:00+00:00  506.865082  499.983463

[1088 rows x 2 columns]
                                close  Mean Price  Standard Deviation  \
Date                                                                    
2020-01-02 00:00:00+00:00  302.208679  330.000000                 NaN   
2020-01-03 00:00:00+00:00  299.920258  330.000000                 NaN   
2020-01-06 00:00:00+00:00  301.06

                                close  Mean Price  Standard Deviation  \
Date                                                                    
2020-01-02 00:00:00+00:00  302.208679  330.000000                 NaN   
2020-01-03 00:00:00+00:00  299.920258  330.000000                 NaN   
2020-01-06 00:00:00+00:00  301.064423  330.000000                 NaN   
2020-01-07 00:00:00+00:00  300.217957  330.000000                 NaN   
2020-01-08 00:00:00+00:00  301.817993  330.000000                 NaN   
...                               ...         ...                 ...   
2024-04-23 00:00:00+00:00  502.482697  510.263277            7.818523   
2024-04-24 00:00:00+00:00  502.244202  510.116546            7.925441   
2024-04-25 00:00:00+00:00  500.336243  509.923812            8.113810   
2024-04-26 00:00:00+00:00  505.076385  509.708938            8.154808   
2024-04-29 00:00:00+00:00  506.865082  509.575038            8.169616   

                           daily_change   Z-Score 

                                close  Mean Price  Standard Deviation  \
Date                                                                    
2020-01-02 00:00:00+00:00  302.208679  330.000000                 NaN   
2020-01-03 00:00:00+00:00  299.920258  330.000000                 NaN   
2020-01-06 00:00:00+00:00  301.064423  330.000000                 NaN   
2020-01-07 00:00:00+00:00  300.217957  330.000000                 NaN   
2020-01-08 00:00:00+00:00  301.817993  330.000000                 NaN   
...                               ...         ...                 ...   
2024-04-23 00:00:00+00:00  502.482697  507.216174            8.093654   
2024-04-24 00:00:00+00:00  502.244202  507.389752            7.990241   
2024-04-25 00:00:00+00:00  500.336243  507.452584            7.838277   
2024-04-26 00:00:00+00:00  505.076385  507.665765            7.498101   
2024-04-29 00:00:00+00:00  506.865082  507.972967            7.139894   

                           daily_change   Z-Score 

                                close  Mean Price  Standard Deviation  \
Date                                                                    
2020-01-02 00:00:00+00:00  302.208679  330.000000                 NaN   
2020-01-03 00:00:00+00:00  299.920258  330.000000                 NaN   
2020-01-06 00:00:00+00:00  301.064423  330.000000                 NaN   
2020-01-07 00:00:00+00:00  300.217957  330.000000                 NaN   
2020-01-08 00:00:00+00:00  301.817993  330.000000                 NaN   
...                               ...         ...                 ...   
2024-04-23 00:00:00+00:00  502.482697  508.161914            8.778161   
2024-04-24 00:00:00+00:00  502.244202  507.186946            8.343286   
2024-04-25 00:00:00+00:00  500.336243  506.156225            8.121720   
2024-04-26 00:00:00+00:00  505.076385  505.572127            7.652772   
2024-04-29 00:00:00+00:00  506.865082  505.055937            7.566810   

                           daily_change   Z-Score 

...

                                close  Mean Price  Standard Deviation  \
Date                                                                    
2020-01-02 00:00:00+00:00  302.208679  330.000000                 NaN   
2020-01-03 00:00:00+00:00  299.920258  330.000000                 NaN   
2020-01-06 00:00:00+00:00  301.064423  330.000000                 NaN   
2020-01-07 00:00:00+00:00  300.217957  330.000000                 NaN   
2020-01-08 00:00:00+00:00  301.817993  330.000000                 NaN   
...                               ...         ...                 ...   
2024-04-23 00:00:00+00:00  502.482697  510.424261            8.356601   
2024-04-24 00:00:00+00:00  502.244202  510.142287            8.475296   
2024-04-25 00:00:00+00:00  500.336243  509.917278            8.688448   
2024-04-26 00:00:00+00:00  505.076385  509.754022            8.721555   
2024-04-29 00:00:00+00:00  506.865082  509.553498            8.602882   

                           daily_change   Z-Score 

                                close  Mean Price  Standard Deviation  \
Date                                                                    
2020-01-02 00:00:00+00:00  302.208679  330.000000                 NaN   
2020-01-03 00:00:00+00:00  299.920258  330.000000                 NaN   
2020-01-06 00:00:00+00:00  301.064423  330.000000                 NaN   
2020-01-07 00:00:00+00:00  300.217957  330.000000                 NaN   
2020-01-08 00:00:00+00:00  301.817993  330.000000                 NaN   
...                               ...         ...                 ...   
2024-04-23 00:00:00+00:00  502.482697  507.499232            8.038062   
2024-04-24 00:00:00+00:00  502.244202  507.603995            7.846381   
2024-04-25 00:00:00+00:00  500.336243  507.720858            7.568175   
2024-04-26 00:00:00+00:00  505.076385  507.996539            7.215547   
2024-04-29 00:00:00+00:00  506.865082  508.300793            7.170329   

                           daily_change   Z-Score 

                                close  Mean Price  Standard Deviation  \
Date                                                                    
2020-01-02 00:00:00+00:00  302.208679  330.000000                 NaN   
2020-01-03 00:00:00+00:00  299.920258  330.000000                 NaN   
2020-01-06 00:00:00+00:00  301.064423  330.000000                 NaN   
2020-01-07 00:00:00+00:00  300.217957  330.000000                 NaN   
2020-01-08 00:00:00+00:00  301.817993  330.000000                 NaN   
...                               ...         ...                 ...   
2024-04-23 00:00:00+00:00  502.482697  506.764475            8.499792   
2024-04-24 00:00:00+00:00  502.244202  505.930353            8.081719   
2024-04-25 00:00:00+00:00  500.336243  504.941587            8.067826   
2024-04-26 00:00:00+00:00  505.076385  504.642845            7.525980   
2024-04-29 00:00:00+00:00  506.865082  504.122999            6.884909   

                           daily_change   Z-Score 

                                close  Mean Price  Standard Deviation  \
Date                                                                    
2020-01-02 00:00:00+00:00  302.208679  330.000000                 NaN   
2020-01-03 00:00:00+00:00  299.920258  330.000000                 NaN   
2020-01-06 00:00:00+00:00  301.064423  330.000000                 NaN   
2020-01-07 00:00:00+00:00  300.217957  330.000000                 NaN   
2020-01-08 00:00:00+00:00  301.817993  330.000000                 NaN   
...                               ...         ...                 ...   
2024-04-23 00:00:00+00:00  502.482697  510.255322            7.715260   
2024-04-24 00:00:00+00:00  502.244202  510.020275            7.824387   
2024-04-25 00:00:00+00:00  500.336243  509.820173            7.990448   
2024-04-26 00:00:00+00:00  505.076385  509.776920            8.026509   
2024-04-29 00:00:00+00:00  506.865082  509.622760            8.037428   

                           daily_change   Z-Score 

                                close  Mean Price  Standard Deviation  \
Date                                                                    
2020-01-02 00:00:00+00:00  302.208679  330.000000                 NaN   
2020-01-03 00:00:00+00:00  299.920258  330.000000                 NaN   
2020-01-06 00:00:00+00:00  301.064423  330.000000                 NaN   
2020-01-07 00:00:00+00:00  300.217957  330.000000                 NaN   
2020-01-08 00:00:00+00:00  301.817993  330.000000                 NaN   
...                               ...         ...                 ...   
2024-04-23 00:00:00+00:00  502.482697  506.444287            8.585630   
2024-04-24 00:00:00+00:00  502.244202  506.556567            8.479995   
2024-04-25 00:00:00+00:00  500.336243  506.635710            8.160796   
2024-04-26 00:00:00+00:00  505.076385  506.941828            7.945890   
2024-04-29 00:00:00+00:00  506.865082  507.195800            7.817246   

                           daily_change   Z-Score 